Visualizando los queries, keys y values

In [1]:
from transformers import AutoTokenizer
from bertviz.transformers_neuron_view import BertModel
from bertviz.neuron_view import show

In [2]:
model_ckpt = 'bert-base-uncased'
tokenizer = AutoTokenizer.from_pretrained(model_ckpt)
model = BertModel.from_pretrained(model_ckpt)

In [3]:
text = 'time flies like an arrow'

In [4]:
show(model, 'bert', tokenizer, text, display_mode='dark', layer=0, head=8)

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

# Transformer

In [5]:
inputs = tokenizer(text, return_tensors='pt', add_special_tokens=False)
inputs.input_ids

tensor([[ 2051, 10029,  2066,  2019,  8612]])

con *add_special_tokens* en False evitamos que se adicionen los token especiales como CLS y SEP

In [6]:
from torch import nn
from transformers import AutoConfig

In [7]:
config = AutoConfig.from_pretrained(model_ckpt)
token_emb = nn.Embedding(config.vocab_size, config.hidden_size)
token_emb

Embedding(30522, 768)

Creamos los embeddings para que ningún valor esté en cero, conocido como DENSE embeddings si no serían SPARSE

In [8]:
inputs_embeds = token_emb(inputs.input_ids)
inputs_embeds.size()

torch.Size([1, 5, 768])

La salida es [batch_size, seq_len (cantidad de tokens), hidden_dim (tamanho de salida)]

In [9]:
import torch
from math import sqrt

In [10]:
query = key = value = inputs_embeds
dim_k = key.size(-1)

In [11]:
scores = torch.bmm(query, key.transpose(1, 2)) / sqrt(dim_k)
scores.size()

torch.Size([1, 5, 5])

como resultado se tiene una matriz de scores

In [12]:
scores[0]

tensor([[26.3782,  1.1542,  0.9130,  1.5657,  1.0241],
        [ 1.1542, 27.6747,  0.5113, -0.0695,  0.2399],
        [ 0.9130,  0.5113, 30.8040,  0.1597,  0.7932],
        [ 1.5657, -0.0695,  0.1597, 27.9555, -0.8920],
        [ 1.0241,  0.2399,  0.7932, -0.8920, 27.6043]],
       grad_fn=<SelectBackward0>)

In [13]:
import torch.nn.functional as F

In [14]:
weights = F.softmax(scores, dim=-1)
weights.sum(dim=-1)

tensor([[1., 1., 1., 1., 1.]], grad_fn=<SumBackward1>)

In [15]:
attn_outputs = torch.bmm(weights, value)
attn_outputs.shape

torch.Size([1, 5, 768])

In [16]:
def scaled_dot_product_attention(query, key, value):
    dim_k = key.size(-1)
    scores = torch.bmm(query, key.transpose(1, 2)) / sqrt(dim_k)
    weights = F.softmax(scores, dim=-1)
    return torch.bmm(weights, value)

Si hacemos esa relacion tomando q, k y v igual el problema es que vamos a asignar el mismo espacio y probabilidad a todos

In [17]:
class AttentionHead(nn.Module):
    def __init__(self, embed_dim, head_dim):
        super().__init__()
        self.q = nn.Linear(embed_dim, head_dim)
        self.k = nn.Linear(embed_dim, head_dim)
        self.v = nn.Linear(embed_dim, head_dim)

    def forward(self, hidden_state):
        attn_outputs = scaled_dot_product_attention(
            self.q(hidden_state), self.k(hidden_state), self.v(hidden_state)
        )
        return attn_outputs

el nn.Linear toma las dimensiones embed_dim (ultima dimension) las lleva a head_dim, para reducirla y que sean independientes, luego se aprenderan esos valores

ese hidden_state tiene [batch, seq_length, embed_dim], debemos tener el embed_dim igual del que entra en el constructor para que no haya error


In [18]:
class MultiHeadAttention(nn.Module):
    def __init__(self, config):
        super().__init__()
        # Config en este ejemplo
        embed_dim = config.hidden_size
        num_heads = config.num_attention_heads
        head_dim = embed_dim // num_heads
        self.heads = nn.ModuleList(
            [AttentionHead(embed_dim, head_dim) for _ in range(num_heads)]
        )
        self.output_linear = nn.Linear(embed_dim, embed_dim)

    def forward(self, hidden_state):
        x = torch.cat([h(hidden_state) for h in self.heads], dim=-1)
        x = self.output_linear(x)
        return x

In [19]:
multihead_attn = MultiHeadAttention(config)
attn_output = multihead_attn(inputs_embeds)
attn_output.size()

torch.Size([1, 5, 768])

In [20]:
from bertviz import head_view
from transformers import AutoModel

In [21]:
model = AutoModel.from_pretrained(model_ckpt, output_attentions=True)

In [22]:
sentence_a = 'time flies like an arrow'
sentence_b = 'fruit flies like a banana'

In [23]:
viz_inputs = tokenizer(sentence_a, sentence_b, return_tensors='pt')

In [24]:
attention = model(**viz_inputs).attentions
sentence_b_start = (viz_inputs.token_type_ids == 0).sum(dim=1)
tokens = tokenizer.convert_ids_to_tokens(viz_inputs.input_ids[0])

In [25]:
head_view(attention, tokens, sentence_b_start, heads=[8])

<IPython.core.display.Javascript object>